In [2]:
from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister, transpile, Aer, IBMQ, assemble
from qiskit.tools.jupyter import *
from qiskit.visualization import *
from ibm_quantum_widgets import *
from qiskit.providers.aer import QasmSimulator

import numpy as np

In [3]:
def initialise(bits, index = 0, dictionary = False):
    # instantiate a register with the required number of qubits, nad appropriate labels
    qa = QuantumRegister(bits, 'a')
    qb = QuantumRegister(bits + 1, 'b')
    qc = QuantumRegister(bits, 'carry')
    mod = QuantumRegister(bits, 'mod')
    temp = QuantumRegister(1, 'ctrl_0')
    qx = QuantumRegister(bits, 'output')
    ctrl = QuantumRegister(1, 'ctrl_1')
    exp = QuantumRegister(bits, 'input')
    kickbit = QuantumRegister(1, 'kickbit')
    
    if dictionary == True:
        # add additional qubits and bits as needed if using a dictionary
        clas = ClassicalRegister(index)
        index = QuantumRegister(index, 'index')
        return QuantumCircuit(qa, qb, qc, mod, temp, qx, ctrl, exp, kickbit, index, clas)  
    
    else:
        # add additional bits as needed if not using a dictionary
        clas = ClassicalRegister(bits)
        return QuantumCircuit(qa, qb, qc, mod, temp, qx, ctrl, exp, kickbit, clas)  

def inp(qc, X):
    # input on the exponent register, used for testing that
    # the modular exponentiation circuit functions correctly
    
    bits = len(X)
    xpwr_reg = list(range(5*bits+3, 6*bits+3))

    X = X[::-1]
        
    for i in range(bits):    
        if str(X)[i] == '1':
            qc.x(xpwr_reg[i]) 
            
def Hadamard(qc, bits, index, dictionary = False):
    # act a Hadamard transform on the exponent register,
    # generating a superposition of states
    
    xpwr_reg = list(range(5*bits+3, 6*bits+3))
    index_reg = list(range(6*bits+4, 6*bits+4+index))
    
    if dictionary == False:
        for i in range(bits):
            qc.h(xpwr_reg[i])
    elif dictionary == True:
        for i in range(index):
            qc.h(index_reg[i])
            
def adder(bits):
    # return a ripple carry adder circuit, composed of 4 bit carry circuits
    # and 3 bit summation circuits
    
    qc = QuantumCircuit(3*bits+1)
    
    b_reg_shift = bits 
    c_reg_shift = 2*bits + 1
    
    
    #compute carry bits
    for i in range(bits):
        final_carry = 1 + i + c_reg_shift if i < bits-1 else 1 + i + b_reg_shift
        
        qc.ccx(i,  i + b_reg_shift, final_carry)
        qc.cx(i, i + b_reg_shift)
        qc.ccx(i + c_reg_shift, i + b_reg_shift, final_carry)
        
    qc.cx(bits-1, bits + b_reg_shift - 1)
    
    # compute sum whilst uncomputing carry bits
    for i in range(bits - 1, -1, -1):
        qc.cx(i, i + b_reg_shift)
        qc.cx(i + c_reg_shift, i + b_reg_shift)
        
        if i > 0:
            qc.ccx(i + c_reg_shift - 1, i + b_reg_shift - 1, i + c_reg_shift)
            qc.cx(i - 1, i + b_reg_shift - 1)
            qc.ccx(i - 1, i + b_reg_shift - 1, i + c_reg_shift)
    
    adder = qc.to_gate()
    adder.name = "Adder"
    
    return adder

def adderinv(bits):
    # reversed operation addition circuit, effectively a subtraction circuit
    
    return adder(bits).reverse_ops()

def modadder(N):
    # Modular adder constructed from adder and inverse adder circuits
    
    # initialise
    bits = len(N)
    qc = QuantumCircuit(4*bits+2)
    
    # name registers for convenience 
    a_reg = list(range(bits))
    b_reg = list(range(bits, 2*bits+1))
    carry_reg = list(range(2*bits+1, 3*bits+1))
    N_reg = list(range(3*bits+1, 4*bits+1))
    
    b_msb = 2*bits
    
    control_bit = 4*bits+1
        
    qc.append(adder(bits),a_reg+b_reg+carry_reg)
    qc.append(adderinv(bits),N_reg+b_reg+carry_reg)
    qc.x(b_msb)
    qc.cx(b_msb, control_bit)
    qc.x(b_msb)
    
    for bit in zip(N[::-1], N_reg):
        if bit[0] == '1':
            qc.cx(control_bit, bit[1])
    
    qc.append(adder(bits),N_reg+b_reg+carry_reg)
    
    for bit in zip(N[::-1], N_reg):
        if bit[0] == '1':
            qc.cx(control_bit, bit[1])

    qc.append(adderinv(bits), a_reg+b_reg+carry_reg)
    qc.cx(b_msb, control_bit)
    qc.append(adder(bits), a_reg+b_reg+carry_reg)

    mod_adder = qc.to_gate()
    mod_adder.name = 'ModaddN'
    
    return mod_adder
       
def modmul(A, N):
    # modular multiplier circuit construced from repeated modular additions
    
    # inititialise
    bits = len(N)
    qc = QuantumCircuit(5*bits+3)
    
    # name registers for convenience 
    a_reg = list(range(bits))
    b_reg = list(range(bits, 2*bits+1))
    X_reg = list(range(4*bits+2, 5*bits+2))
    cont_bit = 5*bits+2

    for i in range(bits):
        
        # precompute 2^i * A * x_i
        Ax = format((int(A, 2)*2**i)%int(N, 2), '#010b')[-bits:][::-1]
        
        # instantiate appropriate controls, making the addition controlled
        for j in range(bits):
            if Ax[j] == '1':
                qc.ccx(cont_bit, X_reg[i], a_reg[j]) 
        
        # instantiate modular adder on precomputed value
        qc.append(modadder(N), range(qc.width()-(bits + 1)))
        
        # repeat instantiated controls, ensuring the register is cleared for later use
        for j in range(bits):
            if Ax[j] == '1':
                qc.ccx(cont_bit, X_reg[i], a_reg[j]) 
    
    # copy x input to output register if control bit is set to 0
    qc.x(cont_bit)
    for i in range(bits):   
        qc.ccx(X_reg[i], cont_bit, b_reg[i])
        
    qc.x(cont_bit)
        
    mod_mul = qc.to_gate()
    mod_mul.name = str(int(A, 2))+'XMod'+str(int(N, 2))
                
    return mod_mul

def modexp(A, N):
    
    # modular exponentiation circuit consrtructed form repeated modular multiplications
    
    # initialise
    bits = len(N)
    
    qa = QuantumRegister(bits, 'a')
    qb = QuantumRegister(bits + 1, 'b')
    qc = QuantumRegister(bits, 'carry')
    mod = QuantumRegister(bits, 'modN')
    temp = QuantumRegister(1, 'temp')
    qx = QuantumRegister(bits, 'x_prod')
    ctrl = QuantumRegister(1, 'ctrl')
    exp = QuantumRegister(bits, 'x_exp')
    
    qc = QuantumCircuit(qa, qb, qc, mod, temp, qx, ctrl, exp)
    
    # name registers for convenience
    N_reg = list(range(3*bits + 1, 4*bits + 1))
    xprod_reg = list(range(4*bits+2,5*bits+2))
    ctrl = 5*bits+2
    xpwr_reg = list(range(5*bits+3, 6*bits+3))

    # reverse input to account for reading direction differing from indexing direction    
    N = N[::-1]
    
    # initialise product register in state 00..001
    qc.x(xprod_reg[0])
    
    # input modulus
    for i in range(bits):    
        if str(N)[i] == '1':
            qc.x(N_reg[i])    
    
    # compute modular multiplication for each of the input values
    for i in range(bits):
        
        # precompute 2^i * A * x_i
        A_i = format((int(A, 2)**(2**i)%int(N, 2)), '#010b')[-bits:]
        
        # precompute modular inverse of 2^i * A * x_i
        A_i_inv = format(pow(int(A, 2)**(2**i)%int(N, 2), -1, int(N, 2)), '#010b')[-bits:]
        
        # make activation dependant on control bit
        qc.cx(xpwr_reg[i], ctrl) 
        
        # compute product of precomputed value with current value on register modulo N
        qc.append(modmul(A_i, N), list(range(5*bits+3)))
    
        # swap input and output registers
        for k in range(bits):
            qc.swap(bits + k, 4*bits + 2 + k)
        
        # clear output register using reversed circuit affecting multiplication of 
        # multiplicative inverse of A_i modulo N
        qc.append(modmul(A_i_inv, N).reverse_ops(), list(range(5*bits + 3)))

        # remove dependancy on control bit
        qc.cx(xpwr_reg[i], ctrl) 
        
    # clear modulus
    for i in range(bits):    
        if str(N)[i] == '1':
            qc.x(N_reg[i])  
            
    modexp = qc.to_gate()
    modexp.name = '('+str(int(A, 2))+'^X)Mod'+str(int(N, 2))
                
    return modexp

def diffuser(bits):
    #initialise
    qc = QuantumCircuit(bits)
    
    # perform rotation
    for i in range(bits):
        qc.h(i)
        qc.x(i)
        
    qc.h(bits-1)
    qc.mct(list(range(bits-1)), bits-1)  
    qc.h(bits-1)
    
    for i in range(bits):
        qc.x(i)
        qc.h(i)
        
    diffuser= qc.to_gate()
    diffuser.name = "Diffuser"
    return diffuser

In [4]:
def dictionary(bits = 3, index = 2):
    # only works for bits = 3, index = 2
    # represents a dictionary {00:001, 01:010, 10:011, 11:110} from a pair of indexing qubits alpha and beta
    
    #initialise
    qc = QuantumCircuit(bits+index)

    # name registers for convenience
    xpwr_reg = list(range(bits))
    index_reg = list(range(bits,bits+index)) #index qubits alpha and beta
    
    #0th bit is set to NOT beta
    qc.x(index_reg[0])
    qc.cx(index_reg[0], xpwr_reg[0])
    qc.x(index_reg[0])
    
    #1st bit is set to alpha OR beta
    qc.ccx(index_reg[0],index_reg[1], xpwr_reg[1])
    qc.cx(index_reg[0], xpwr_reg[1])
    qc.cx(index_reg[1], xpwr_reg[1])

    #2nd bit is set to alpha AND beta
    qc.ccx(index_reg[0],index_reg[1], xpwr_reg[2])
   
    
    dictionary = qc.to_gate()
    dictionary.name = 'R'
    
    return dictionary
       

In [5]:
# define number of bits used for elements of search space and
# number fo bits used by index.
bits = 3
index = 2

# initialise
qc = initialise(bits, index, 1)

# name registers for convenience
output_reg = list(range(4*bits+2, 5*bits+2))
input_reg  = list(range(5*bits+3, 6*bits+3))
index_reg = list(range(6*bits+4, 6*bits+4+index))
 
# define base, modulus and clause
A = '011'
N = '111'
clause = 0 #clause is defined by stating which elements of the output should be zero, in this case 110

# create superposition on index register
Hadamard(qc, bits, index, 1)
# apply dictionary operator to index register, creating superposition of dict elements on input register
qc.append(dictionary(), list(range(5*bits + 3, 6*bits + 3)) + list(range(6*bits+4, 6*bits+4+index)))
# apply modular exponentiation circuit to input register
qc.append(modexp(A,N), list(range(6*bits+3)))

# initialise kickbit
qc.x(6*bits+3)
qc.h(6*bits+3)
# initialise clause
qc.x(np.array(range(4*bits+2,5*bits+2))[clause])
# act multi-controlled-Toffoli gate on output register
qc.mct(list(range(4*bits+2,5*bits+2)), 6*bits+3)
#remove clause
qc.x(np.array(range(4*bits+2,5*bits+2))[clause])
# reset kickbit
qc.h(6*bits+3)
qc.x(6*bits+3)

# apply inverse modular exponentiation circuit
qc.append(modexp(A,N).reverse_ops(), list(range(6*bits+3)))
# clear dictionary output
qc.append(dictionary(), list(range(5*bits + 3, 6*bits + 3)) + list(range(6*bits+4, 6*bits+4+index)))
# apply diffuser to index register
qc.append(diffuser(index), list(range(6*bits+4, 6*bits+4+index)))
# measure index register
qc.measure(index_reg, list(range(index)))

# transpile and simulate
simulator = QasmSimulator()
compiled_circuit = transpile(qc, simulator)
job = simulator.run(compiled_circuit, shots = 1000)
result = job.result()
counts = result.get_counts(compiled_circuit)


print('calculating', int(A, 2), 'to the x mod ', int(N, 2))
print('output of reg is:', counts)
display(qc.draw())

# Dictionary operator contains the index entry pairs {00:001, 01:010, 10:011, 11:110}
# Grover search returns the index 10, corresponding to entry 011 bin = 3 dec
# 3^3 mod 7 = 6 dec = 110 bin, so that this is indeed the solution state.
# Note that since the superposition generated by the Hadamard transform 
# on a 3 digit register creates a superposition contains 8 elements, conducting this search 
# would ordinarily have required more than one Grover round demonstrating that a dictionary 
# allows for a reduced operation count. 

calculating 3 to the x mod  7
output of reg is: {'10': 1000}


┌─────────────┐               ┌─────────────────────┐»
     a_0: ───────────┤0            ├───────────────┤0                    ├»
                     │             │               │                     │»
     a_1: ───────────┤1            ├───────────────┤1                    ├»
                     │             │               │                     │»
     a_2: ───────────┤2            ├───────────────┤2                    ├»
                     │             │               │                     │»
     b_0: ───────────┤3            ├───────────────┤3                    ├»
                     │             │               │                     │»
     b_1: ───────────┤4            ├───────────────┤4                    ├»
                     │             │               │                     │»
     b_2: ───────────┤5            ├───────────────┤5                    ├»
                     │             │               │                     │»
     b_3: ───────────┤6            ├───────────────┤6                    ├»
                     │             │               │                     │»
 carry_0: ───────────┤7            ├───────────────┤7                    ├»
                     │             │               │                     │»
 carry_1: ───────────┤8            ├───────────────┤8                    ├»
                     │             │               │                     │»
 carry_2: ───────────┤9            ├───────────────┤9                    ├»
                     │             │               │                     │»
   mod_0: ───────────┤10 (3^X)Mod7 ├───────────────┤10 (3^X)Mod7_reverse ├»
                     │             │               │                     │»
   mod_1: ───────────┤11           ├───────────────┤11                   ├»
                     │             │               │                     │»
   mod_2: ───────────┤12           ├───────────────┤12                   ├»
                     │             │               │                     │»
  ctrl_0: ───────────┤13           ├───────────────┤13                   ├»
                     │             │┌───┐     ┌───┐│                     │»
output_0: ───────────┤14           ├┤ X ├──■──┤ X ├┤14                   ├»
                     │             │└───┘  │  └───┘│                     │»
output_1: ───────────┤15           ├───────■───────┤15                   ├»
                     │             │       │       │                     │»
output_2: ───────────┤16           ├───────■───────┤16                   ├»
                     │             │       │       │                     │»
  ctrl_1: ───────────┤17           ├───────┼───────┤17                   ├»
               ┌────┐│             │       │       │                     │»
 input_0: ─────┤0   ├┤18           ├───────┼───────┤18                   ├»
               │    ││             │       │       │                     │»
 input_1: ─────┤1   ├┤19           ├───────┼───────┤19                   ├»
               │    ││             │       │       │                     │»
 input_2: ─────┤2   ├┤20           ├───────┼───────┤20                   ├»
          ┌───┐│  R │└────┬───┬────┘     ┌─┴─┐┌───┐└────────┬───┬────────┘»
 kickbit: ┤ X ├┤    ├─────┤ H ├──────────┤ X ├┤ H ├─────────┤ X ├─────────»
          ├───┤│    │     └───┘          └───┘└───┘         └───┘         »
 index_0: ┤ H ├┤3   ├─────────────────────────────────────────────────────»
          ├───┤│    │                                                     »
 index_1: ┤ H ├┤4   ├─────────────────────────────────────────────────────»
          └───┘└────┘                                                     »
    c0: 2/════════════════════════════════════════════════════════════════»
                                                                          »
«                                   
«     a_0: ─────────────────────────
«                                   
«     a_1: ───────────────────────

In [6]:
# define number of bits used for elements of search space and
# number fo bits used by index.
bits = 3
index = 0

# initialise
qc = initialise(bits, index, 0)

# name registers for convenience
output_reg = list(range(4*bits+2, 5*bits+2))
input_reg  = list(range(5*bits+3, 6*bits+3))
 
# define base, modulus and clause
A = '011'
N = '111'
clause = 0 #clause is defined by stating which elements of the output should be zero, in this case 110

# create superposition on index register
Hadamard(qc, bits, index, 0)
# apply modular exponentiation circuit to input register
qc.append(modexp(A,N), list(range(6*bits+3)))

# initialise kickbit
qc.x(6*bits+3)
qc.h(6*bits+3)
# initialise clause
qc.x(np.array(range(4*bits+2,5*bits+2))[clause])
# act multi-controlled-Toffoli gate on output register
qc.mct(list(range(4*bits+2,5*bits+2)), 6*bits+3)
#remove clause
qc.x(np.array(range(4*bits+2,5*bits+2))[clause])
# reset kickbit
qc.h(6*bits+3)
qc.x(6*bits+3)

# apply inverse modular exponentiation circuit
qc.append(modexp(A,N).reverse_ops(), list(range(6*bits+3)))
# clear dictionary output
# apply diffuser to index register
qc.append(diffuser(bits), input_reg)
# measure index register
qc.measure(input_reg, list(range(bits)))

# transpile and simulate
simulator = QasmSimulator()
compiled_circuit = transpile(qc, simulator)
job = simulator.run(compiled_circuit, shots = 1000)
result = job.result()
counts = result.get_counts(compiled_circuit)


print('calculating', int(A, 2), 'to the x mod ', int(N, 2))
print('output of reg is:', counts)
display(qc.draw())

# A single Grover iteration applied to the same problem, without the use of a 
# dictionary operator. The output is no longer composed of a single state, as 
# the search space contains twice as many elements. This demonstrates
# the functionality of the dictionary operator.

calculating 3 to the x mod  7
output of reg is: {'000': 20, '111': 26, '011': 793, '001': 24, '101': 36, '010': 36, '110': 34, '100': 31}


┌─────────────┐               ┌─────────────────────┐»
     a_0: ─────┤0            ├───────────────┤0                    ├»
               │             │               │                     │»
     a_1: ─────┤1            ├───────────────┤1                    ├»
               │             │               │                     │»
     a_2: ─────┤2            ├───────────────┤2                    ├»
               │             │               │                     │»
     b_0: ─────┤3            ├───────────────┤3                    ├»
               │             │               │                     │»
     b_1: ─────┤4            ├───────────────┤4                    ├»
               │             │               │                     │»
     b_2: ─────┤5            ├───────────────┤5                    ├»
               │             │               │                     │»
     b_3: ─────┤6            ├───────────────┤6                    ├»
               │             │               │                     │»
 carry_0: ─────┤7            ├───────────────┤7                    ├»
               │             │               │                     │»
 carry_1: ─────┤8            ├───────────────┤8                    ├»
               │             │               │                     │»
 carry_2: ─────┤9            ├───────────────┤9                    ├»
               │             │               │                     │»
   mod_0: ─────┤10 (3^X)Mod7 ├───────────────┤10 (3^X)Mod7_reverse ├»
               │             │               │                     │»
   mod_1: ─────┤11           ├───────────────┤11                   ├»
               │             │               │                     │»
   mod_2: ─────┤12           ├───────────────┤12                   ├»
               │             │               │                     │»
  ctrl_0: ─────┤13           ├───────────────┤13                   ├»
               │             │┌───┐     ┌───┐│                     │»
output_0: ─────┤14           ├┤ X ├──■──┤ X ├┤14                   ├»
               │             │└───┘  │  └───┘│                     │»
output_1: ─────┤15           ├───────■───────┤15                   ├»
               │             │       │       │                     │»
output_2: ─────┤16           ├───────■───────┤16                   ├»
               │             │       │       │                     │»
  ctrl_1: ─────┤17           ├───────┼───────┤17                   ├»
          ┌───┐│             │       │       │                     │»
 input_0: ┤ H ├┤18           ├───────┼───────┤18                   ├»
          ├───┤│             │       │       │                     │»
 input_1: ┤ H ├┤19           ├───────┼───────┤19                   ├»
          ├───┤│             │       │       │                     │»
 input_2: ┤ H ├┤20           ├───────┼───────┤20                   ├»
          ├───┤└────┬───┬────┘     ┌─┴─┐┌───┐└────────┬───┬────────┘»
 kickbit: ┤ X ├─────┤ H ├──────────┤ X ├┤ H ├─────────┤ X ├─────────»
          └───┘     └───┘          └───┘└───┘         └───┘         »
    c1: 3/══════════════════════════════════════════════════════════»
                                                                    »
«                                
«     a_0: ──────────────────────
«                                
«     a_1: ──────────────────────
«                                
«     a_2: ──────────────────────
«                                
«     b_0: ──────────────────────
«                                
«     b_1: ──────────────────────
«                                
«     b_2: ──────────────────────
«                                
«     b_3: ──────────────────────
«                                
« carry_0: ──────────────────────
«                                
« carry_1: ──────────────────────
«                                
« carry_2: ──────────────────────
«                                
«   mod_0: 